**multi-link pendulum - python simulation and animation of a multi-link pendulum**

This jupyter notebook uses Lagrange formalism to derive the dynamics of a multi-link pendulum and simulates the like. Unfortanetly, it seems to be not very time-performant, so the best I could do in a reasonable amount of time was 5 links.

> [1] 1994 - Murray, Li, Sastry: *A Mathematical Introduction to Robotic Manipulation* (https://www.cds.caltech.edu/~murray/books/MLS/pdf/mls94-complete.pdf)


Notes:
*   indexing starts with zero
*   angular positions and velocities are defined absolutely (in general joint based measurements of a link orientation is relative to the previous link)


(Benjamin Jahn, TU Ilmenau, 2021)

# Initilization

**initialization:** clear workspace, define latex use for display

In [253]:
# clear workspace
%reset -f

In [254]:
# latex math display
from IPython.display import Math

def latexDisplay(latex_obj): display(Math(latex_obj))

# Kinematics and Dynamics

**symbolic computation of the dynamics of a multi-link pendulum:** derive dynamics using Lagrange equations of the second kind [1, p.168ff]

In [255]:
# import sympy for symbolic computations
from sympy import *

In [256]:
# NUMBER OF LINKS (PUT THE DESIRED NUMBER OF LINKS HERE)
N = 5

In [257]:
# generalized coordinates
q = Matrix([Symbol('q_' + str(i), real=True) for i in range(0,N)])
dq = Matrix([Symbol('\dot{q}_' + str(i), real=True) for i in range(0,N)])
ddq = Matrix([Symbol('\ddot{q}_' + str(i), real=True) for i in range(0,N)])

In [258]:
# time dependency and 
t = symbols('t', real=True, positiv=True); # time

# generalized coordinates as function of time
q_t = Matrix([Function('q_' + str(i), real=True)(t) for i in range(0,N)])
dq_t = Matrix([Function('\dot{q}_' + str(i), real=True)(t) for i in range(0,N)])
ddq_t = Matrix([Function('\ddot{q}_' + str(i), real=True)(t) for i in range(0,N)])

# dictionary for substiution
q_t2s = dict(zip(q_t,q)); q_s2t = dict(zip(q,q_t))
dq_t2s = dict(zip(dq_t,dq)); dq_s2t = dict(zip(dq,dq_t))
ddq_t2s = dict(zip(ddq_t,ddq)); ddq_s2t = dict(zip(ddq,ddq_t))

# substitute derivatives
q2dq = dict(zip([diff(q,t) for q in q_t], dq_t))
dq2ddq = dict(zip([diff(dq,t) for dq in dq_t], ddq_t))

In [259]:
# kinematic parameter
l = MatrixSymbol('l', N, 1); a = MatrixSymbol('a', N, 1)

# dynamic parameter
J = MatrixSymbol('J', N, 1); m = MatrixSymbol('m', N, 1); d = MatrixSymbol('d', N, 1)
grav = symbols('g', real=True, positiv=True) # gravitational constant

In [260]:
# planar rotation
def rot(q): return Matrix([[cos(q), -sin(q)],[sin(q), cos(q)]])

In [261]:
# center of mass postions
p = zeros(2,N)
for i in range(0,N):
  for j in range(0, i):
    p[:,i] = p[:,i] + rot(q_t[j])*Matrix([0, l[j]])
  p[:,i] = p[:,i]  + rot(q_t[i])*Matrix([0, a[i]])
# latexDisplay(r'p =' + latex(p.subs(q_t2s)))

In [262]:
# center of mass velocities
dp = diff(p, t).subs(q2dq)
#latexDisplay(r'\dot{p} =' + latex(dp.subs(q_t2s).subs(dq_t2s)))

In [263]:
# kinetic and potential energy
T = sum([(Rational(1,2)*dp.col(i).T*m[i]*dp.col(i))[0] for i in range(0,N)]) + (Rational(1,2)*q.T*diag(*J)*q)[0] #; T = simplify(T)
V = sum([(m[i]*Matrix([0, grav]).T*p.col(i))[0] for i in range(0,N)]) #; V = simplify(V)
#latexDisplay(r'T =' + latex(T.subs(q_t2s).subs(dq_t2s)))
#latexDisplay(r'V =' + latex(V.subs(q_t2s).subs(dq_t2s)))

In [264]:
# Lagrangian --> ODE
L = T-V
Lode = diff(Matrix([L]).jacobian(dq_t),t) - Matrix([L]).jacobian(q_t); Lode = Lode.T
Lode = Lode.subs(q2dq).subs(dq2ddq)

In [265]:
# rephrase as robotic equation of motion
M = Lode.jacobian(ddq_t)
M = factor(M)
C = Rational(1, 2) * (Lode - M * ddq_t).jacobian(dq_t)
g = Lode - M * ddq_t - C * dq_t
g = simplify(g)
D = (diag(*d) + diag(*[*d[1:], 0])
    + Matrix(N, N, lambda i, j: -d[i] if i == j + 1 else 0) + Matrix(N, N, lambda i, j: -d[i + 1] if i + 1 == j else 0))
# ode = M.LUsolve(-C*dq_t-D*dq_t-g); ode = ode.subs(q_t2s).subs(dq_t2s)


# Simulation

In [266]:
# numerics imports
import numpy as np
from math import ceil, floor
from scipy.integrate import solve_ivp

In [267]:
# numeric values for parameters
l_num = np.linspace(0.5, 0.35, N) # length of links [m]
a_num = l_num*1/2 # distance to center-of-mass for each link [m]
m_num = np.linspace(1,0.5, N,) # mass of each link [kg]
J_num = np.linspace(0.02, 0.01, N,) # moment-of-inertia for each link [kg m^2]
d_num = np.ones(N)*0.005 # viscous friction coefficient [Nm s]
grav_num = 9.81; # gravitational constant [m^3 (kg s^2)^-1]

substitutions = dict(zip([*l, *a, *m, *J, *d, grav],[*l_num, *a_num, *m_num, *J_num, *d_num, grav_num]))
#ode = ode.subs(substitutions)
M_num = M.subs(substitutions)
C_num = C.subs(substitutions)
g_num = g.subs(substitutions)
D_num = D.subs(substitutions)   

ode = M_num.LUsolve(-C_num*dq_t-D_num*dq_t-g_num); ode = ode.subs(q_t2s).subs(dq_t2s)

In [268]:
# prepared ode for solve_ivp
ode_sys = Matrix([*dq, *ode]) # express odes of order two as system of odes of order one
ode_f = lambdify([*q, *dq], [*ode_sys])

In [269]:
# execute simulation
T = 12; Ts = 1e-3
x0 = np.zeros(2*N); x0[-1] = 0.04
t_ = np.linspace(0,T, ceil(T/Ts+1), endpoint=True)

# solve ode without any input and nominal parameters
sol = solve_ivp(lambda t,x: ode_f(*x), [0,t_[-1]], x0, 'RK45', t_eval = t_, rtol=1e-5); 

# Plots

In [270]:
# plot imports
import plotly.graph_objs as go
import plotly.io as pio
pio.templates.default = "none"
pio.renderers.default = "notebook_connected"

In [271]:
# define generic plot function for angular position of triple pendulum
from colour import Color

def plot_pendulum(sol):
    start_color = '#0000ff'; end_color = '#00ff80'
    colorscale = [x.hex for x in list(Color(start_color).range_to(Color(end_color), N))]

    fig = go.Figure()
    for idx in range(0, N):
        fig.add_trace(go.Scatter(x=sol.t, y=sol.y[idx, :] / np.pi, name=r"$\varphi_" + str(idx) + "$", line=dict(width=2, color=colorscale[idx])))

    fig.update_layout(height=600, width=1000, xaxis=dict(title=r"$\text{time in seconds}$"),
        yaxis=dict(title=r"$\text{angular position in } \pi \text{ rad}$", tickmode="linear", tick0=0.0, dtick=1))

    fig.show()

In [272]:
# plot angular positions
plot_pendulum(sol)

# Animation

In [273]:
## import matplotlib for animations
import matplotlib.pyplot as plt
from matplotlib import animation, rc, cm
rc('animation', html='jshtml')

In [274]:
# define pendulum animation function
def animate_pendulum(sol, fps=25, colormap='winter'):

  colors = cm.get_cmap(colormap, N)

  # frame number and index distance for given fps (tried to avoid interpolation to not slow down animation even further)
  T2anim = sol.t[-1]
  frameNumber = fps*T2anim
  didx = floor(len(sol.t)/frameNumber)

  # create and setup figure
  fig, ax = plt.subplots(figsize=(14,10))
  plt.axis('equal'); plt.close()
  l_sum = sum(l_num)
  ax.set_xlim((-l_sum*1.65, l_sum*1.65)); ax.set_ylim((-l_sum*1.35, l_sum*1.35))

  # create line objects
  line_base, = ax.plot([], [], lw=3, c=(0, 0, 0))
  lines = [None]*N
  for idx in range(0,N):
    lines[idx], = ax.plot([], [], lw=4, c=colors(idx/N))

  # initialization function: plot the background of each frame
  def init():
    # draw rail
    line_base.set_data(np.linspace(-l_sum*1.65, l_sum*1.65, 10), 0*np.linspace(-2, 2, 10)) 
    
    return (line_base,*lines, ) # return line objects

  # animation function: this is called sequentially
  def animate(i):

    # current configuration of pendulum
    p = np.zeros((2,N+1))
    for idx in range(1,N+1):
      p[:,idx] = p[:,idx-1] + np.array([-l_num[idx-1]*sin(sol.y[idx-1,i*didx]), l_num[idx-1]*cos(sol.y[idx-1,i*didx])])

    for idx in range(0,N):
      lines[idx].set_data([p[0,idx], p[0, idx+1]],[p[1,idx], p[1, idx+1]])

    return (*lines,) # return line objects

  # return animation object
  return animation.FuncAnimation(fig, animate, init_func=init, frames=floor(frameNumber), interval=1/fps*1000, blit=True)


In [275]:
anim = animate_pendulum(sol) # no control input --> cart fixed in position
anim 